In [ ]:
import warnings
warnings.filterwarnings("ignore",category =RuntimeWarning)
import numpy as np
import makeqx as mkq
import de2 as de
import multiprocessing as mp
    
def arc_0(qx, lam_min=400, lam_max=800, npoints=50):
    cthick = qx[0]
    q_x = qx[1:]
    Rs0, Rp0 = mkq.tmm_lam_parallel(q_x, cthick, 0, n_par=12, lam_low=lam_min, lam_high=lam_max, lam_pts=npoints, n_subs=1.52)
    return np.mean(Rs0)
    
def arc_dig_0(qx, lam_min=400, lam_max=800, npoints=50):
    cthick = qx[0]
    q_x = mkq.digitize_qx(qx[1:], dlevels=2)
    Rs0, Rp0 = mkq.tmm_lam_parallel(q_x, cthick, 0, n_par=12, lam_low=lam_min, lam_high=lam_max, lam_pts=npoints, n_subs=1.52)
    return np.mean(Rs0)


def tmm_wrapper2(arg):
    args, kwargs = arg
    return mkq.tmm_eval_wsweep(*args, **kwargs)


def arc_par(pop, **kwargs):
    jobs = []
    pool=mp.Pool(12)
    for indiv in pop:
        indivi = mkq.digitize_qx(indiv[1:], dlevels=2)
        jobs.append((indivi, indiv[0], 0))
    arg = [(j, kwargs) for j in jobs]
    answ = np.array(pool.map(tmm_wrapper2, arg))
    pool.close()
    return np.mean(answ, axis=1)

    
num_layers = 40
bnds = [(0, 1)]*num_layers
bnds = [(300, 400)] + bnds
its_first = 0
psnew = 500
its_second = 500

pop = np.ones((psnew, 1+ num_layers))
for indiv in range(psnew):
    pop[indiv,1:] = mkq.make_qx(num_layers)
    pop[indiv,0] = 500 
    
b, c, hstry = de.de_cp(fobj=arc_par, bounds=bnds, pop=pop, history=[], it_start=its_first, popsize=psnew, its=its_second, lam_low=400, lam_high=800, lam_pts=50)


#m1 = mkq.tmm_eval2(qx=pop[0][1:], cthick=pop[0][0]) 
#m2 = mkq.tmm_eval(qx=pop[0][1:], cthick=pop[0][0]) 

#arc_par(pop, lam_low=400, lam_high=800, lam_pts=50)

0 3.5364400617784897
5 2.824247002189513
10 2.3462630380353606
15 1.9657988439545293
20 1.7431834173401826
25 1.5548321006945318
30 1.4273202243105385
35 1.324341384452208
40 0.792594549254551
45 0.792594549254551
50 0.792594549254551
55 0.6011330622003288
60 0.6011330622003288
65 0.5913752343291452
70 0.5913752343291452
75 0.5913752343291452
80 0.5913752343291452
85 0.5913752343291452
90 0.49733505560725083
95 0.49733505560725083
100 0.49733505560725083
105 0.49733505560725083
110 0.49733505560725083
115 0.49733505560725083
120 0.49733505560725083
125 0.49733505560725083
130 0.49733505560725083
135 0.49733505560725083
140 0.49733505560725083
145 0.49733505560725083
150 0.4092137422382544
155 0.4092137422382544


In [ ]:
np.savetxt(X=b, fname='b.txt')